# Prepare Flickr API Batch CSV

In [1]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
from glob import glob, iglob
from pathlib import Path
from tqdm import tqdm_notebook as tqdm

import pandas as pd

## Create CSV for API

| photo_id |
|:---|
| 12234 |

In [12]:
# flickr api data
fp_in_flickr_meta = '/data_store_hdd/datasets/people/ibm_dif/research/flickr_api_query_dump.csv'
# ibm count data
fp_in_ibm_meta = '/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_metadata.csv'
# output
fp_out = '/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_metadata.csv'

In [68]:
# load ibm data and create count lookup with photoid
df_ibm_meta = pd.read_csv(fp_in_ibm_meta)
ibm_meta_records = df_ibm_meta.to_dict('records')
count_lookup = {}
for ibm_meta_record in ibm_meta_records:
  photo_id = int(Path(ibm_meta_record['url']).stem.split('_')[0])
  count_lookup[photo_id] = ibm_meta_record['count']

In [69]:
len(count_lookup)

100438

In [70]:
results = []

In [71]:
df_flickr_meta = pd.read_csv(fp_in_flickr_meta, dtype={'count': int, 'username': str, 'sha256': str}).fillna('')
flickr_meta_records = df_flickr_meta.to_dict('records')

In [74]:
# load flickr data
for flickr_meta_record in flickr_meta_records:
  try:
    nsid = flickr_meta_record['nsid']
    photo_id = int(flickr_meta_record['photo_id'])
    count = count_lookup[photo_id]
  except Exception as e:
    print(f'Error: {e}, {flickr_meta_record}')
    continue
  obj = {
    'photo_id': photo_id,
    'nsid': nsid,
    'count': count 
  }
  results.append(obj)

Error: invalid literal for int() with base 10: '', {'country': '', 'description': 'Haircut Next...', 'lat': '', 'lon': '', 'nsid': '', 'owner_location': '', 'path_alias': '', 'photo_id': '', 'place': '', 'place_id': '', 'posted': '', 'realname': '', 'taken': '', 'username': '', 'woeid': ''}
Error: invalid literal for int() with base 10: '', {'country': '', 'description': '', 'lat': '86085317@N00', 'lon': 'New York', 'nsid': 'anonymousthomas', 'owner_location': '4975598', 'path_alias': '', 'photo_id': '', 'place': '1108685469', 'place_id': 'Thomas', 'posted': '2005-02-18 00:11:09', 'realname': 'anonymousthomas', 'taken': '', 'username': '', 'woeid': ''}


In [75]:
df_out = pd.DataFrame.from_dict(results)
df_out.to_csv(fp_out, index=False)

## Create meta count file

In [6]:
fp_flickr_api_dump = '/data_store_hdd/datasets/people/ibm_dif/research/flickr_api_query_dump.csv'
fp_out_meta = '/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_flickr_meta.csv'

In [3]:
df = pd.read_csv(fp_flickr_api_dump)
groups = df.groupby('nsid')

/home/adam/anaconda3/envs/megapixels/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3020: DtypeWarning: Columns (2,3,10) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [5]:
results = []
for nsid, group in groups:
  obj = {
    'nsid': nsid,
    'count': len(group)
  }
  results.append(obj)

In [7]:
pd.DataFrame.from_dict(results).to_csv(fp_out_meta, index=False)